In [1]:
import pandas as pd
import re
import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
from pymorphy3 import MorphAnalyzer
from nltk.corpus import stopwords
import numpy as np
import torch.nn as nn
from sklearn.model_selection import train_test_split
import torch

In [3]:
stopwords = stopwords.words('russian')

In [4]:
df = pd.read_csv('./data/Petitions.csv')
df

id                               public_petition_text  \
0      3168490                                     снег на дороге   
1      3219678                очистить кабельный киоск от рекламы   
2      2963920  Просим убрать все деревья и кустарники, которы...   
3      3374910  Неудовлетворительное состояние парадной - надп...   
4      3336285                                           Граффити   
...        ...                                                ...   
59884  3128111                           прошу закрасить граффити   
59885  3276713       Прошу вас отремонтировать пешеходную дорожку   
59886  3274663  Необходимо демонтировать незаконную рекламную ...   
59887  3359308  Очень гремит на ветру металлическая часть окна...   
59888  3209098  Две проблемы в одном:\n1) Незаконные надписи/о...   

                                         reason_category  
0                                        Благоустройство  
1                                        Благоустройство  
2                                        Благоустройство  
3                                         Содержание МКД  
4                                        Благоустройство  
...                                                  ...  
59884                                    Благоустройство  
59885                                    Благоустройство  
59886  Незаконная информационная и (или) рекламная ко...  
59887                                             Кровля  
59888                                    Благоустройство  

[59889 rows x 3 columns]

In [5]:
print(len(df['reason_category'].unique()), "\n", df['reason_category'].value_counts())

15 
 reason_category
Благоустройство                                                                     34769
Содержание МКД                                                                      14461
Нарушение правил пользования общим имуществом                                        2170
Незаконная информационная и (или) рекламная конструкция                              1831
Фасад                                                                                1483
Повреждения или неисправность элементов уличной инфраструктуры                       1164
Кровля                                                                                825
Водоснабжение                                                                         809
Состояние рекламных или информационных конструкций                                    673
Санитарное состояние                                                                  434
Центральное отопление                                                          

In [6]:
df.drop(columns="id", inplace=True)

In [7]:
new_df = df.sample(100)
new_df

public_petition_text  \
43695  Огромные лужи на тротуаре.\nНе пройти! Скаплив...   
44159  Смёт на проезжей части.\nТребуется произвести ...   
28714                    старая листва и мусор на газоне   
28897                                  Надписи на двери.   
8330                        Просьба заменить крышку люка   
...                                                  ...   
59661  В подъезде N 10 на первом этаже (рядом с лифто...   
10882  Граффити на дверях лифта на 5-м этаже а так же...   
32756  вырван пульт аварийного вызова на балконе втор...   
37797  дверь контейнерной площадки не безопасна. Чтоб...   
21338  Очистить дорожные знаки от самоклея, не оставл...   

                                         reason_category  
43695                                    Благоустройство  
44159                                    Благоустройство  
28714                                    Благоустройство  
28897                                    Благоустройство  
8330   Повреждения или неисправность элементов улично...  
...                                                  ...  
59661                                     Содержание МКД  
10882                                     Содержание МКД  
32756                                     Содержание МКД  
37797                                     Содержание МКД  
21338                                    Благоустройство  

[100 rows x 2 columns]

In [8]:
X = new_df["public_petition_text"].to_list()
y = new_df["reason_category"].to_list()

In [9]:
text1 = ['<p> Привет, чурка! Также Я: любл%ю тебя; и был @$, но не ты дурак</p>', 'Привет, чурка, я в Дубае']

In [28]:
# html_tag=re.compile('<.*?>')
# text = html_tag.sub('', text)
# text

In [10]:
def preprocessing_text(text):
    lst = []
    #remove html
    for i in text:
        html_tag=re.compile('<.*?>')
        text_no_html = html_tag.sub('', i)
        #remove quots
        text_only_letters = re.sub('[^\w\s]', '', text_no_html)
        #tokenizим
        words = word_tokenize(text_only_letters)
        #morphим
        morph = MorphAnalyzer()
        lemmas = [morph.normal_forms(w)[0] for w in words]
        #del_sw
        prepared = [w for w in lemmas if w not in stopwords]
        lemm_sentce = ' '.join(prepared)
        lst.append(lemm_sentce)
        # lst.append(prepared)
    return lst


In [70]:
prepro_text = preprocessing_text(text=X)
prepro_text

['огромный лужа тротуар пройти скапливаться ежедневно требоваться принять мера устранение действенный ликвидировать причина образование фотофиксация 2203прилагаться',
 'смёт проезжий часть требоваться произвести работа качественный механизировать уборка пч фотофиксация прилагаться',
 'старый листва мусор газон',
 'надпись дверь',
 'просьба заменить крышка люк',
 'работать домофон подъезд 5',
 'просить очистить технический средство организация дорожный движение объявление',
 'образование плесень жилой помещение вследствие протечка крыша xxxxxxxx xxx этаж 9 лестница 3',
 'удалить пенить сломать дерево',
 'ужасный состояние дорога двор дом будапештский ул 29к1',
 'перегореть лампочка 3 этаж 3 подъезд',
 'ветка дом 78 пр ветеран аптека петербургский аптека',
 'вода подвал 4 парадный теплоцентр обращаться жкс ваш сайт несколько проблема обращение вода выкачивать спустя короткий время вода снова появляться ощущение вода откачивать причина появление вода решать просьба разобраться добрый день

In [71]:
count_vocab = set((' '.join(prepro_text).split()))
word_to_ix = {word: i for i, word in enumerate(count_vocab)}
word_to_ix

{'переулок': 0,
 'дефект': 1,
 'труба': 2,
 'переходить': 3,
 'неудовлетворительный': 4,
 'управлять': 5,
 '29к1': 6,
 'надлежащий': 7,
 'вид4': 8,
 'сухой': 9,
 'кратковременный': 10,
 'кв12': 11,
 'повод': 12,
 'мыться': 13,
 'снять': 14,
 'покрасить': 15,
 'внутренний': 16,
 'край': 17,
 'светофор': 18,
 'огромный': 19,
 'весь': 20,
 'организация': 21,
 'д1517': 22,
 'минута': 23,
 'александр': 24,
 'вопрос': 25,
 'автомобилист': 26,
 'слой': 27,
 'разрушениявыкрашивание': 28,
 '11': 29,
 'покрытие': 30,
 'фотография': 31,
 'ремонт': 32,
 '35к1': 33,
 '33': 34,
 'появление': 35,
 'необходимо': 36,
 'лестница': 37,
 'вонь': 38,
 'помещение': 39,
 'указанный': 40,
 'чистка': 41,
 'требоваться': 42,
 'цвет': 43,
 'миазмы': 44,
 'решить': 45,
 'клей': 46,
 'водосточный': 47,
 'внутрь': 48,
 'получить': 49,
 'однако': 50,
 'неисправный': 51,
 'очень': 52,
 'газон': 53,
 'противный': 54,
 'восстановить': 55,
 'никуда': 56,
 'видеть': 57,
 'стёкла': 58,
 'доблесть': 59,
 'галочка': 60,
 'с

In [58]:
word_list = list(word_to_ix.keys())
word_list

['переулок',
 'дефект',
 'труба',
 'переходить',
 'неудовлетворительный',
 'управлять',
 '29к1',
 'надлежащий',
 'вид4',
 'сухой',
 'кратковременный',
 'кв12',
 'повод',
 'мыться',
 'снять',
 'покрасить',
 'внутренний',
 'край',
 'светофор',
 'огромный',
 'весь',
 'организация',
 'д1517',
 'минута',
 'александр',
 'вопрос',
 'автомобилист',
 'слой',
 'разрушениявыкрашивание',
 '11',
 'покрытие',
 'фотография',
 'ремонт',
 '35к1',
 '33',
 'появление',
 'необходимо',
 'лестница',
 'вонь',
 'помещение',
 'указанный',
 'чистка',
 'требоваться',
 'цвет',
 'миазмы',
 'решить',
 'клей',
 'водосточный',
 'внутрь',
 'получить',
 'однако',
 'неисправный',
 'очень',
 'газон',
 'противный',
 'восстановить',
 'никуда',
 'видеть',
 'стёкла',
 'доблесть',
 'галочка',
 'сильно',
 'пломба',
 'настоящий',
 'талый',
 'мусор',
 'отверстие',
 'тсодда',
 'качественный',
 'здравствуйте',
 'подключение',
 'фото',
 'отказываться',
 'ужасный',
 '9й',
 '8а',
 'перчаткиуберит',
 'сообщение',
 'кладка',
 'прошлое'

In [305]:
with open('word_list3.tsv', 'w', encoding='utf-8') as f:
    f.write('\n'.join(word_list))

In [131]:
dframe = pd.DataFrame(prepro_text, columns=['X'])
dframe

X
0   двор дом арка свальный крупногабаритный мусор ...
1                                  яма проезжий часть
2   развалиться светильник входной дверь парадный ...
3                                            очистить
4   подъезд дом установить конструкция показ рекла...
..                                                ...
95                                             листва
96  заявка 2965322 заявка требование убрать листва...
97  здравствуйте просить рассмотреть возможность у...
98  вблизи остановка общественный транспорт проспе...
99                шина газон дом 1713 улица оборонный

[100 rows x 1 columns]

In [132]:
dframe['Y'] = y

In [133]:
dframe

X  \
0   двор дом арка свальный крупногабаритный мусор ...   
1                                  яма проезжий часть   
2   развалиться светильник входной дверь парадный ...   
3                                            очистить   
4   подъезд дом установить конструкция показ рекла...   
..                                                ...   
95                                             листва   
96  заявка 2965322 заявка требование убрать листва...   
97  здравствуйте просить рассмотреть возможность у...   
98  вблизи остановка общественный транспорт проспе...   
99                шина газон дом 1713 улица оборонный   

                                                 Y  
0                                  Благоустройство  
1                                  Благоустройство  
2                                   Содержание МКД  
3                                   Содержание МКД  
4   Нарушение порядка пользования общим имуществом  
..                                             ...  
95                                 Благоустройство  
96                                 Благоустройство  
97                                 Благоустройство  
98                                 Благоустройство  
99                                 Благоустройство  

[100 rows x 2 columns]

In [38]:
def embedding_matrix(f):
    count_vocab = set((' '.join(f).split()))
    print(len(count_vocab))
    word_to_ix = {word: i for i, word in enumerate(count_vocab)}
    print(word_to_ix)
    a = max(word_to_ix.values()) + 1
    print(a)
    matrica = [[0] * a for _ in range(a)]
    for k in range(0, len(f)):
        b = len(f[k].split())
        words = f[k].split()
        for i in range(b):
            for j in range(i+1, b):
                if words[i] in f[k] and words[j] in f[k]:
                    matrica[word_to_ix[words[i]]][word_to_ix[words[j]]] += 1
                    matrica[word_to_ix[words[j]]][word_to_ix[words[i]]] += 1

    # for row in matrica:
    #     print(row)
    
    return matrica

In [39]:
emb_matr = embedding_matrix(prepro_text)
emb_matr

692
{'кругом': 0, 'подстанция': 1, '23': 2, 'изпод': 3, 'проходимость': 4, 'образоваться': 5, 'разрешать': 6, 'xxxxxxxxxxxxx': 7, 'забитый': 8, 'открыть': 9, 'ремонт': 10, 'куст': 11, 'утро': 12, 'больший': 13, 'мыть': 14, 'дать': 15, 'систематически': 16, 'иметь': 17, 'связь': 18, 'левый': 19, 'цокольный': 20, 'желательно': 21, 'день': 22, 'земля': 23, 'большой': 24, 'сегодняшний': 25, 'устранить': 26, 'вблизи': 27, '3101': 28, 'эвакуация': 29, 'хотеться': 30, 'щит': 31, 'единственный': 32, 'ям': 33, 'сообщение': 34, 'работа': 35, 'поворот': 36, '6111': 37, 'заявка': 38, 'мусор': 39, 'д9': 40, '293': 41, 'отклонить': 42, 'загромождать': 43, 'листва': 44, 'территория': 45, 'весельный': 46, 'цвет': 47, 'картонный': 48, 'требоваться': 49, 'фаза': 50, 'нужда': 51, 'снег': 52, 'урна': 53, 'висеть': 54, 'обмотка': 55, 'балкон': 56, 'красота': 57, 'яма': 58, 'который': 59, 'рф': 60, '29': 61, 'xxxxxxx': 62, 'грунт': 63, 'площадь': 64, 'двор': 65, 'проваливаться': 66, 'согласие': 67, 'зачисти

[[0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  2,
  0,
  0,
  1,
  2,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  1,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,
  0,


In [40]:
from sklearn.decomposition import PCA

In [45]:
pca = PCA(n_components=30)
pca.fit(emb_matr)
data_pca = pca.transform(emb_matr)

In [47]:
np.savetxt('embeddings.tsv', data_pca, delimiter='\t')

## Neural_buri

In [14]:
count_vocab2 = set((' '.join(prepro_text).split()))
print(len(count_vocab2))
word_to_ix2 = {word: i for i, word in enumerate(count_vocab2)}
word_to_ix2

732


{'переулок': 0,
 'дефект': 1,
 'труба': 2,
 'переходить': 3,
 'неудовлетворительный': 4,
 'управлять': 5,
 '29к1': 6,
 'надлежащий': 7,
 'вид4': 8,
 'сухой': 9,
 'кратковременный': 10,
 'кв12': 11,
 'повод': 12,
 'мыться': 13,
 'снять': 14,
 'покрасить': 15,
 'внутренний': 16,
 'край': 17,
 'светофор': 18,
 'огромный': 19,
 'весь': 20,
 'организация': 21,
 'д1517': 22,
 'минута': 23,
 'александр': 24,
 'вопрос': 25,
 'автомобилист': 26,
 'слой': 27,
 'разрушениявыкрашивание': 28,
 '11': 29,
 'покрытие': 30,
 'фотография': 31,
 'ремонт': 32,
 '35к1': 33,
 '33': 34,
 'появление': 35,
 'необходимо': 36,
 'лестница': 37,
 'вонь': 38,
 'помещение': 39,
 'указанный': 40,
 'чистка': 41,
 'требоваться': 42,
 'цвет': 43,
 'миазмы': 44,
 'решить': 45,
 'клей': 46,
 'водосточный': 47,
 'внутрь': 48,
 'получить': 49,
 'однако': 50,
 'неисправный': 51,
 'очень': 52,
 'газон': 53,
 'противный': 54,
 'восстановить': 55,
 'никуда': 56,
 'видеть': 57,
 'стёкла': 58,
 'доблесть': 59,
 'галочка': 60,
 'с

In [15]:
lookup = {value: key for key, value in word_to_ix2.items()}
lookup

{0: 'переулок',
 1: 'дефект',
 2: 'труба',
 3: 'переходить',
 4: 'неудовлетворительный',
 5: 'управлять',
 6: '29к1',
 7: 'надлежащий',
 8: 'вид4',
 9: 'сухой',
 10: 'кратковременный',
 11: 'кв12',
 12: 'повод',
 13: 'мыться',
 14: 'снять',
 15: 'покрасить',
 16: 'внутренний',
 17: 'край',
 18: 'светофор',
 19: 'огромный',
 20: 'весь',
 21: 'организация',
 22: 'д1517',
 23: 'минута',
 24: 'александр',
 25: 'вопрос',
 26: 'автомобилист',
 27: 'слой',
 28: 'разрушениявыкрашивание',
 29: '11',
 30: 'покрытие',
 31: 'фотография',
 32: 'ремонт',
 33: '35к1',
 34: '33',
 35: 'появление',
 36: 'необходимо',
 37: 'лестница',
 38: 'вонь',
 39: 'помещение',
 40: 'указанный',
 41: 'чистка',
 42: 'требоваться',
 43: 'цвет',
 44: 'миазмы',
 45: 'решить',
 46: 'клей',
 47: 'водосточный',
 48: 'внутрь',
 49: 'получить',
 50: 'однако',
 51: 'неисправный',
 52: 'очень',
 53: 'газон',
 54: 'противный',
 55: 'восстановить',
 56: 'никуда',
 57: 'видеть',
 58: 'стёкла',
 59: 'доблесть',
 60: 'галочка',
 61

In [16]:
num_emb = list(lookup.keys())
len(num_emb)

732

In [17]:
embs = nn.Embedding(len(num_emb), 3)
input = torch.tensor(num_emb)

In [18]:
import torch.nn.functional as F

In [66]:
def generate_context_word_pairs(corpus, window_size, vocab_size):
    context_length = window_size*2
    for words in corpus:
        print(words)
        sentence_length = len(corpus)
        print(sentence_length)
        for index, word in enumerate(corpus):
            context_words = []
            label_word = []
            start = index - window_size

            end = index + window_size + 1
            context_words.append([corpus[i] for i in range(start, end) if 0 <= i < sentence_length and i != index])
            label_word.append(word)
            print(context_words)
            print(label_word)
            # x = context_words
            # y = label_word, vocab_size
            # yield (x, y)
            return 0

In [68]:
generate_context_word_pairs(word_list, 4, len(count_vocab2))

переулок
732
[['дефект', 'труба', 'переходить', 'неудовлетворительный']]
['переулок']


0

In [29]:
class CBOWModeler(nn.Module):

    def __init__(self, vocab_size, embedding_dim, context_size):
        super(CBOWModeler, self).__init__()
        self.embeddings = nn.Embedding(vocab_size, embedding_dim)
        self.linear1 = nn.Linear(context_size * embedding_dim, 250)
        self.linear2 = nn.Linear(250, vocab_size)

    def forward(self, inputs):
        embeds = self.embeddings(inputs).view((1, -1))
        out1 = F.relu(self.linear1(embeds))
        out2 = self.linear2(out1)           
        log_probs = F.log_softmax(out2, dim=1)
        return log_probs

    # def predict(self,input):
    #     context_idxs = torch.tensor([word_to_ix2[w] for w in input], dtype=torch.long)
    #     res = self.forward(context_idxs)
    #     # res_arg = torch.argmax(res)
    #     res_val, res_ind = res.sort(descending=True)
    #     res_val = res_val[0][:5]
    #     res_ind = res_ind[0][:5]
    #     #print(res_val)
    #     #print(res_ind)
    #     for arg in zip(res_val,res_ind):
    #         #print(arg)
    #         print([(key,val,arg[0]) for key,val in word_to_ix2.items() if val == arg[1]])

In [34]:
loss_function = nn.NLLLoss()

In [36]:
model = CBOWModeler(len(num_emb), 10, 3)
model

CBOWModeler(
  (embeddings): Embedding(732, 10)
  (linear1): Linear(in_features=30, out_features=250, bias=True)
  (linear2): Linear(in_features=250, out_features=732, bias=True)
)

In [37]:
optimizer = torch.optim.SGD(model.parameters(), lr=0.001)

In [33]:
model.predict(['двор', 'арка', 'лист'])

[('выставить', 223, tensor(-5.9189, grad_fn=<UnbindBackward0>))]
[('ветка', 293, tensor(-5.9689, grad_fn=<UnbindBackward0>))]
[('продолжаться', 637, tensor(-6.0765, grad_fn=<UnbindBackward0>))]
[('переходить', 3, tensor(-6.1115, grad_fn=<UnbindBackward0>))]
[('11', 29, tensor(-6.1420, grad_fn=<UnbindBackward0>))]


In [227]:
wordvecs = model.linear2.weight.cpu().detach().numpy()
wordvecs

array([[ 0.0251831 , -0.02891936, -0.03031075, ...,  0.03528842,
        -0.03260382,  0.03102396],
       [ 0.05762857, -0.05076442, -0.04819339, ..., -0.00330954,
         0.05132478,  0.017945  ],
       [ 0.04069733, -0.01938121, -0.05274904, ...,  0.02470092,
        -0.04803883,  0.04907109],
       ...,
       [-0.0528859 , -0.01634015,  0.03947989, ..., -0.01430494,
         0.04670191,  0.0130012 ],
       [-0.05101476, -0.01645047, -0.01007505, ...,  0.00647969,
         0.01355693,  0.00826564],
       [ 0.00495719,  0.05280975, -0.0389386 , ...,  0.03492624,
         0.00658961,  0.03668834]], dtype=float32)

In [228]:
np.savetxt('word2vec_vectors.tsv', wordvecs, delimiter='\t')

In [205]:
dframe['X'][0].split()

['двор',
 'дом',
 'арка',
 'свальный',
 'крупногабаритный',
 'мусор',
 'большой',
 'количество',
 'картонный',
 'коробка',
 'xxxxxxxxxxxxx',
 'xxxxxx',
 'xxxxxxxxxx',
 'x',
 'xxxxxxxxxxxxx',
 'xxxxxxxxxxx',
 'сегодняшний',
 'день',
 '03042021',
 'мусор',
 'убрать',
 'количество',
 'увеличиться',
 'проблема',
 'устранить']

In [ ]:
epochs = 5

loss_values = []
for epoch in range(epochs):
    for x_b, y_b in train_dl:

        outputs = model(x_b)

        loss_value = loss_function(outputs, y_b)

        loss_value.backward()

        optimizer.step()

        optimizer.zero_grad()
    loss_values.append(loss_value.item())

    print(f'Эпоха {epoch + 1}, Значение функции потерь: {loss_value.item()}')